In [27]:
import requests
from bs4 import BeautifulSoup
import pandas as pd
from concurrent.futures import ThreadPoolExecutor

def fetch_medicamento(url):
    response = requests.get(url)
    if response.status_code == 200:
        return response.text
    else:
        return None

def process_medicamento(medicamento):
    try:
        nome = medicamento.find("h1", class_="name").text.strip()
    except:
        nome = None
    try: 
        preco = float(medicamento.find("p", class_="unit-price").text.replace('R$ ', '').replace(',', '.'))
    except: 
        preco = 0
    try: 
        desconto = float(medicamento.find("span", class_="descont").find('span').text.replace('%', '').replace('-',''))
    except: 
        desconto = 0
    try:
        preco_desconto = round(preco * (1-desconto/100), 2)
    except:
        preco_desconto = 0
    try:
        ean = medicamento.find("meta", itemprop_='gtin13').get('content')
    except:
        ean = None
    try:
        marca = medicamento.find("a", class_="text-primary font-weight-bold mr-3").text.strip()
    except:
        marca = None


    return nome, preco, preco_desconto, desconto, ean, marca


def main():
    URLS=[]
    urls_primaria = []
    for i in range(1, 156):
        # URL da página de medicamentos
        urls_primaria.append("https://www.farmaponte.com.br/medicamentos/?p="+str(i))

    with ThreadPoolExecutor(max_workers=10) as executor:
        responses_primaria = list(executor.map(fetch_medicamento, urls_primaria))
        
        for response in responses_primaria:
            # Criar objeto BeautifulSoup
            soup = BeautifulSoup(response, "html.parser")
            # Encontrar os containers dos medicamentos
            medicamentos = soup.find_all("div", class_="li")
            # Extrair dados para cada medicamento

            for medicamento in medicamentos:
                add = medicamento.find("a", class_='item-image').get('href') 
                URL = "https://www.farmaponte.com.br" + add
                URLS.append(URL)
                
    print(len(URLS))
    print(URLS[0])

    NOME = []
    PRECO=[]
    PRECO_DESCONTO = []
    DESCONTO = []
    EAN=[]
    MARCA=[]

    with ThreadPoolExecutor(max_workers=12) as executor:
        responses = list(executor.map(fetch_medicamento, URLS))
        
        for response in responses:
            soup = BeautifulSoup(response, "html.parser")
            medicamentos = soup.find_all("div", class_="content")
            for medicamento in medicamentos:
                nome, preco, preco_desconto, desconto, ean, marca = process_medicamento(medicamento)
                NOME.append(nome)
                PRECO.append(preco)
                PRECO_DESCONTO.append(preco_desconto)
                DESCONTO.append(desconto)
                EAN.append(ean)
                MARCA.append(marca)

    df = pd.DataFrame()
    df['Nome'] = NOME
    df['Preço sem desconto'] = PRECO
    df['Preço com desconto'] = PRECO_DESCONTO
    df['Desconto (porcentagem)'] = DESCONTO 
    df['Código EAN'] = EAN
    df['Marca'] = MARCA
    print(df)
    df.to_csv('base_farmaponte.csv')

    return df



In [28]:
df = main()

3100
https://www.farmaponte.com.br/dipirona-gts-10ml-ger/p
                                                   Nome  Preço sem desconto  \
0                            Dipirona Gotas 10ml Germed                6.93   
1     Dipirona Monoidratada Biosintética - Aché 50mg...               16.78   
2     Citrato de Sildenafila Medley 50mg, caixa com ...               17.51   
3     Tadalafila Eurofarma 5mg, caixa com 30 comprim...              347.64   
4     Tadalafila Eurofarma 20mg, caixa com 4 comprim...              185.37   
...                                                 ...                 ...   
3095           Torval CR 300mg caixa com 30 comprimidos               46.48   
3096           Torval CR 500mg caixa com 30 comprimidos               77.62   
3097  Pristiq 50mg 28 Comprimidos Revestidos de Libe...              233.36   
3098                          Amato 25mg 60 Comprimidos               57.54   
3099         Azitromicina 500mg Eurofarma 3 Comprimidos               48

In [30]:
# Carregar o arquivo CSV como um DataFrame
df.to_csv("Drogaria_VeraCruz.csv", index=False)

# Exibir as primeiras linhas do DataFrame para verificar se foi carregado corretamente
df.head()

Nome  Preço sem desconto  \
0                         Dipirona Gotas 10ml Germed                6.93   
1  Dipirona Monoidratada Biosintética - Aché 50mg...               16.78   
2  Citrato de Sildenafila Medley 50mg, caixa com ...               17.51   
3  Tadalafila Eurofarma 5mg, caixa com 30 comprim...              347.64   
4  Tadalafila Eurofarma 20mg, caixa com 4 comprim...              185.37   

   Preço com desconto  Desconto (porcentagem) Código EAN Marca  
0                6.93                       0       None  None  
1               16.78                       0       None  None  
2               17.51                       0       None  None  
3              347.64                       0       None  None  
4              185.37                       0       None  None

In [19]:
URLS=[]
urls_primaria = []
for i in range(1, 156):
    # URL da página de medicamentos
    urls_primaria.append("https://www.farmaponte.com.br/medicamentos/?p="+str(i))

with ThreadPoolExecutor(max_workers=10) as executor:
    responses_primaria = list(executor.map(fetch_medicamento, urls_primaria))
    
    for response in responses_primaria:
        # Criar objeto BeautifulSoup
        soup = BeautifulSoup(response, "html.parser")
        # Encontrar os containers dos medicamentos
        medicamentos = soup.find_all("div", class_="li")
        # Extrair dados para cada medicamento

        for medicamento in medicamentos:
            print(medicamento)
            add = medicamento.find("a", class_='item-image').get('href') 
            print(add)
            URL = "https://www.farmaponte.com.br" + add
            URLS.append(URL)

<div class="li"><div class="item-product" data-id="sku_22146" data-sku="22146"><a class="item-image" href="/dipirona-gts-10ml-ger/p"><img alt="Dipirona Gotas 10ml Germed" class="img-lazy" data-src="//io.convertiez.com.br/m/farmaponte/shop/products/images/27501/small/dipirona-gts-10ml-ger_22743.jpg" height="224" src="//io.convertiez.com.br/s/farmaponte/img/blank.png" title="Dipirona Gotas 10ml Germed" width="224"/><span class="discount"><span><b>70%</b><small class="d-block">off</small></span></span></a><div class="desc position-relative"><div><div class="seals position-relative"></div><h2 class="title"><a href="/dipirona-gts-10ml-ger/p">
                            Dipirona Gotas 10ml Germed
                        </a></h2><div class="box-prices"><div class="prices"><p class="unit-price mr-2"><span>R$ 6,93</span></p><p class="pix-price"><strong>R$ 2,04</strong> no pix
                                                </p><p class="sale-price">
                                    ou <str

KeyboardInterrupt: 